In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf

In [2]:
sess = tf.InteractiveSession()

In [3]:
data = pd.read_csv("/data/reddit1.csv")

In [4]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer()

In [5]:
predictors = vectorizer.fit_transform(data.body.fillna(""))
labels = data.controversiality

In [9]:
labels = np.vstack([data.controversiality, 1 - data.controversiality]).T

## 1. Placeholders for the data

In [12]:
V = predictors.shape[1]
V

392166

In [39]:
x = tf.placeholder(tf.float32, shape=(None, V))
y = tf.placeholder(tf.int32, shape=(None, 2))

## 2. Specify the graph.

In [40]:
n1 = 100
W1 = tf.Variable(tf.zeros([V, n1]))
b1 = tf.Variable(tf.zeros([n1]))
y1 = tf.nn.relu(tf.matmul(x, W1) + b1)

In [41]:
W2 = tf.Variable(tf.zeros([n1, 2]))
b2 = tf.Variable(tf.zeros([2]))
y2 = tf.matmul(y1, W2) + b2

## 3. Specify the loss function and the optimization.

In [42]:
loss = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(y2, y))

In [ ]:
trainer = tf.train.GradientDescentOptimizer(0.1).minimize(loss)

## 4. Feed in data into this graph.

In [43]:
sess.run(tf.initialize_all_variables())

In [45]:
for i in range(10):
    batch = list(range(i * 1000, (i + 1) * 1000))
    _, loss_vals = sess.run(
        [trainer, loss],
        feed_dict={
            x: predictors[batch].todense(),
            y: labels[batch]
        }
    )
    print(loss_vals)

0.693146
0.648513
0.606435
0.570341
0.537824
0.507177
0.482446
0.454879
0.434125
0.417384


## Evaluate accuracy.

In [49]:
accuracy = tf.reduce_mean(tf.cast(
        tf.equal(tf.argmax(y2, 1), tf.argmax(y, 1)),
        tf.float32
    ))

In [51]:
accuracy.eval(feed_dict={
        x: predictors[-10000:].todense(),
        y: labels[-10000:]
    })

0.97210002

In [52]:
out = tf.argmax(y2, 1).eval(feed_dict={
        x: predictors[-10000:].todense(),
        y: labels[-10000:]
    }
)